In [5]:
import pandas as pd
import numpy as np
import torch
from torch.optim import Adam

import pyreadr
import matplotlib.pyplot as plt
import seaborn as sns
from sklearn.manifold import TSNE
from mpl_toolkits.mplot3d import Axes3D

from dataset import split_trainValTest
from trainer import train_AgeVae, test_AgeVae
from model import VAEAge, TwoLayerNetwork
import random

In [6]:
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
print(device)

data = pd.read_csv("./Data/Aging_data_combined_orthologs.csv")
datawNAN = data.fillna(0)
datawNAN = torch.Tensor(datawNAN.select_dtypes(include=['float64']).iloc[:, :-1].values).to(device)

cuda:0


In [22]:
data.select_dtypes(include=['float64']).head()

22290     19241     22764     26900     20592     21674    170835  \
0 -0.247323  2.507661 -0.541452  1.350328 -0.243283 -0.161073  1.620147   
1 -0.886874  2.376398  0.089364 -1.845986 -0.429977 -0.120847  1.413098   
2 -0.425477  2.486357 -0.267903  1.091088 -0.304483 -0.508611  1.648069   
3 -0.109844  2.485793 -0.257505  1.092448 -0.376999 -0.164930  1.415539   
4 -0.113013  2.483457 -0.663475  1.117652 -0.534237 -0.090691  1.659320   

     245522    223775     29812  ...     21355     74246    245944     70025  \
0 -0.473716  0.569714 -0.079840  ... -0.476725  1.068326 -0.140546  1.264458   
1 -0.240960  1.526477  0.025074  ...  0.465357  0.858500  0.263775  1.165149   
2  0.230987  0.658745  0.219776  ... -0.287755  1.211574  0.319631  1.120054   
3 -0.020269  0.987971  0.234308  ...  0.647168  1.118283  0.417193  1.101575   
4  0.066766  0.916895 -0.078901  ...  0.189340  0.907593  0.358030  1.144129   

      98733     20713     69719     71583  Age_rel_m  Age_m  
0  0.065406 -1.089505  0.354001  0.172595   0.458333   22.0  
1 -0.030337 -0.990064  0.220329  0.108677   0.458333   22.0  
2 -0.044280 -0.505998  0.217979 -0.702106   0.458333   22.0  
3 -0.675073 -0.438833  0.300332  0.066519   0.458333   22.0  
4 -0.417904 -0.944047  0.190206 -0.478423   0.458333   22.0  

[5 rows x 15813 columns]

In [7]:
batch_size = 64
validation_split = .1
test_split = .0
l1_lambda, l2_lambda = 0.03, 0.01
input_size = datawNAN.shape[1] - 1
latent_size = 10
down_channels, up_channels = 2, 2
hidden_size = [10, 20]
lr = 1e-4
epochs = 1000

In [8]:
torch.use_deterministic_algorithms(False)
vae_max = None
current_acc = 0
seed_max = None
metrics_history_max, metrics_history_val_max = [], []
l = list(range(1000))
r = random.sample(l, 10)
for SEED in r:
  random.seed(SEED)
  torch.manual_seed(SEED)
  torch.cuda.manual_seed(SEED)
  np.random.seed(SEED)
  torch.backends.cudnn.deterministic=True
  train_loader, val_loader, test_loader = split_trainValTest(datawNAN, batch_size, validation_split, test_split, SEED)
  AgeModel = TwoLayerNetwork(latent_size, l1_lambda, l2_lambda, hidden_size)
  vae = VAEAge(input_size, AgeModel, latent_size, down_channels, up_channels)
  vae_optim = Adam(vae.parameters(), lr)
  metrics_history, metrics_history_val = train_AgeVae(vae, train_loader, val_loader, batch_size, epochs, vae_optim, device)
  if vae_max is None or current_acc <  metrics_history_val[-1][0]:
    vae_max = vae
    metrics_history_max, metrics_history_val_max = metrics_history, metrics_history_val
    seed_max = SEED

age_pred.shape, age.shape, batch.shape, x_rec.shape, x.shape torch.Size([64]) torch.Size([64]) torch.Size([64, 15812]) torch.Size([64, 15811]) torch.Size([64, 15811])
age_pred[0], age[0], batch_size, age_loss tensor(-0.4407, device='cuda:0', grad_fn=<SelectBackward0>) tensor(0.5322, device='cuda:0') 64 tensor(1.1035, device='cuda:0', grad_fn=<SqrtBackward0>)
Epoch 1 | Age r2: -26.51529047224257 | Age loss: 1.07223778963089 |Age reg: 2.912502931223975 | MSE loss: 12582.930881076389 | R2: -0.45705190632078385 | KLD loss: 17.6633743180169
Epoch 1 | Age r2 val: -25.75592565536499 | Age loss val: 1.0681710541248322 | MSE loss val: 8720.296142578125 | R2 val: -0.023192018270492554 | KLD loss val: 26.289552688598633
age_pred.shape, age.shape, batch.shape, x_rec.shape, x.shape torch.Size([64]) torch.Size([64]) torch.Size([64, 15812]) torch.Size([64, 15811]) torch.Size([64, 15811])
age_pred[0], age[0], batch_size, age_loss tensor(-0.4694, device='cuda:0', grad_fn=<SelectBackward0>) tensor(0.063

Epoch 12 | Age r2: -22.41291692521837 | Age loss: 0.98965984582901 |Age reg: 2.53691158692042 | MSE loss: 2773.322414822049 | R2: 0.6782058311833276 | KLD loss: 51.891785091824005
Epoch 12 | Age r2 val: -20.524435997009277 | Age loss val: 0.9765125811100006 | MSE loss val: 2835.3359985351562 | R2 val: 0.6633239686489105 | KLD loss val: 51.49876689910889
age_pred.shape, age.shape, batch.shape, x_rec.shape, x.shape torch.Size([64]) torch.Size([64]) torch.Size([64, 15812]) torch.Size([64, 15811]) torch.Size([64, 15811])
age_pred[0], age[0], batch_size, age_loss tensor(-0.6889, device='cuda:0', grad_fn=<SelectBackward0>) tensor(0.3750, device='cuda:0') 64 tensor(1.0083, device='cuda:0', grad_fn=<SqrtBackward0>)
Epoch 13 | Age r2: -22.276960531870525 | Age loss: 0.9847575492329068 |Age reg: 2.505462361706628 | MSE loss: 2618.041219075521 | R2: 0.6972010367446475 | KLD loss: 51.732620133294
Epoch 13 | Age r2 val: -20.603455543518066 | Age loss val: 0.9763836711645126 | MSE loss val: 2668.859

Epoch 24 | Age r2: -18.96122958925035 | Age loss: 0.911013149552875 |Age reg: 2.1821550528208413 | MSE loss: 1875.620344373915 | R2: 0.7824657840861214 | KLD loss: 51.85417005750868
Epoch 24 | Age r2 val: -17.922314167022705 | Age loss val: 0.9003800451755524 | MSE loss val: 1992.8914794921875 | R2 val: 0.7672986835241318 | KLD loss val: 51.19653606414795
age_pred.shape, age.shape, batch.shape, x_rec.shape, x.shape torch.Size([64]) torch.Size([64]) torch.Size([64, 15812]) torch.Size([64, 15811]) torch.Size([64, 15811])
age_pred[0], age[0], batch_size, age_loss tensor(-0.5190, device='cuda:0', grad_fn=<SelectBackward0>) tensor(0.0102, device='cuda:0') 64 tensor(0.9198, device='cuda:0', grad_fn=<SqrtBackward0>)
Epoch 25 | Age r2: -18.717148568895126 | Age loss: 0.9068588846259646 |Age reg: 2.1545373996098838 | MSE loss: 1811.16746351454 | R2: 0.790091743071874 | KLD loss: 52.188120947943794
Epoch 25 | Age r2 val: -17.522902011871338 | Age loss val: 0.897466629743576 | MSE loss val: 2029.

Epoch 36 | Age r2: -16.315267191992866 | Age loss: 0.8522658944129944 |Age reg: 1.8708624243736267 | MSE loss: 1508.5050896538628 | R2: 0.8251022464699216 | KLD loss: 53.7570276260376
Epoch 36 | Age r2 val: -15.54982042312622 | Age loss val: 0.8498802483081818 | MSE loss val: 1667.8335266113281 | R2 val: 0.8036681115627289 | KLD loss val: 53.42976951599121
age_pred.shape, age.shape, batch.shape, x_rec.shape, x.shape torch.Size([64]) torch.Size([64]) torch.Size([64, 15812]) torch.Size([64, 15811]) torch.Size([64, 15811])
age_pred[0], age[0], batch_size, age_loss tensor(2.3943, device='cuda:0', grad_fn=<SelectBackward0>) tensor(0.4737, device='cuda:0') 64 tensor(0.8629, device='cuda:0', grad_fn=<SqrtBackward0>)
Epoch 37 | Age r2: -16.21646179093255 | Age loss: 0.8502249899837706 |Age reg: 1.8468031419648065 | MSE loss: 1455.5938212076824 | R2: 0.831509166293674 | KLD loss: 53.70284546746148
Epoch 37 | Age r2 val: -16.57622981071472 | Age loss val: 0.8546585738658905 | MSE loss val: 1741.

Epoch 48 | Age r2: -14.19408761130439 | Age loss: 0.7957680473725001 |Age reg: 1.6013644801245794 | MSE loss: 1270.2494269476997 | R2: 0.8528037799729241 | KLD loss: 54.27805773417155
Epoch 48 | Age r2 val: -13.217377424240112 | Age loss val: 0.7855185717344284 | MSE loss val: 1436.8158874511719 | R2 val: 0.8314092010259628 | KLD loss val: 53.69215679168701
age_pred.shape, age.shape, batch.shape, x_rec.shape, x.shape torch.Size([64]) torch.Size([64]) torch.Size([64, 15812]) torch.Size([64, 15811]) torch.Size([64, 15811])
age_pred[0], age[0], batch_size, age_loss tensor(-0.2387, device='cuda:0', grad_fn=<SelectBackward0>) tensor(0.0625, device='cuda:0') 64 tensor(0.7990, device='cuda:0', grad_fn=<SqrtBackward0>)
Epoch 49 | Age r2: -14.161271307203505 | Age loss: 0.7922422571314706 |Age reg: 1.5807516011926863 | MSE loss: 1267.425087822808 | R2: 0.8526314679119322 | KLD loss: 54.2238565021091
Epoch 49 | Age r2 val: -12.800373792648315 | Age loss val: 0.7754448056221008 | MSE loss val: 14

...

Epoch 948 | Age r2: -0.020923912525177002 | Age loss: 0.20790062472224236 |Age reg: 0.01147608184773061 | MSE loss: 500.79827796088324 | R2: 0.9419188963042365 | KLD loss: 50.66803995768229
Epoch 948 | Age r2 val: -0.0172998309135437 | Age loss val: 0.21509727463126183 | MSE loss val: 586.3228454589844 | R2 val: 0.9294517785310745 | KLD loss val: 51.53111171722412
age_pred.shape, age.shape, batch.shape, x_rec.shape, x.shape torch.Size([64]) torch.Size([64]) torch.Size([64, 15812]) torch.Size([64, 15811]) torch.Size([64, 15811])
age_pred[0], age[0], batch_size, age_loss tensor(0.3397, device='cuda:0', grad_fn=<SelectBackward0>) tensor(0.3490, device='cuda:0') 64 tensor(0.1923, device='cuda:0', grad_fn=<SqrtBackward0>)
Epoch 949 | Age r2: -0.015015174945195517 | Age loss: 0.20674152713682917 |Age reg: 0.011475722822878096 | MSE loss: 509.33878241644965 | R2: 0.9410864462455114 | KLD loss: 50.680240101284454
Epoch 949 | Age r2 val: -0.01395842432975769 | Age loss val: 0.2151803858578205 |

Epoch 960 | Age r2: -0.014080504576365152 | Age loss: 0.20721693626708454 |Age reg: 0.011482275116981732 | MSE loss: 496.9860153198242 | R2: 0.9426030748420291 | KLD loss: 50.68212095896403
Epoch 960 | Age r2 val: -0.010827094316482544 | Age loss val: 0.2163686826825142 | MSE loss val: 583.0692291259766 | R2 val: 0.9303940236568451 | KLD loss val: 51.677913665771484
age_pred.shape, age.shape, batch.shape, x_rec.shape, x.shape torch.Size([64]) torch.Size([64]) torch.Size([64, 15812]) torch.Size([64, 15811]) torch.Size([64, 15811])
age_pred[0], age[0], batch_size, age_loss tensor(0.3398, device='cuda:0', grad_fn=<SelectBackward0>) tensor(0.1250, device='cuda:0') 64 tensor(0.2103, device='cuda:0', grad_fn=<SqrtBackward0>)
Epoch 961 | Age r2: -0.01311476363076104 | Age loss: 0.20773382236560187 |Age reg: 0.011482585738930438 | MSE loss: 495.58987596299914 | R2: 0.9425970365603765 | KLD loss: 50.765509605407715
Epoch 961 | Age r2 val: -0.01328808069229126 | Age loss val: 0.2149772308766842 

Epoch 972 | Age r2: -0.025764432218339708 | Age loss: 0.20710549793309635 |Age reg: 0.011467078648921516 | MSE loss: 490.00238545735675 | R2: 0.943474711643325 | KLD loss: 50.61855051252577
Epoch 972 | Age r2 val: -0.010634809732437134 | Age loss val: 0.21636449918150902 | MSE loss val: 563.9586639404297 | R2 val: 0.9331931173801422 | KLD loss val: 50.98555660247803
age_pred.shape, age.shape, batch.shape, x_rec.shape, x.shape torch.Size([64]) torch.Size([64]) torch.Size([64, 15812]) torch.Size([64, 15811]) torch.Size([64, 15811])
age_pred[0], age[0], batch_size, age_loss tensor(0.3396, device='cuda:0', grad_fn=<SelectBackward0>) tensor(0.2500, device='cuda:0') 64 tensor(0.2137, device='cuda:0', grad_fn=<SqrtBackward0>)
Epoch 973 | Age r2: -0.014588743448257446 | Age loss: 0.2071125821934806 |Age reg: 0.011475723314409455 | MSE loss: 488.49928198920355 | R2: 0.9434492571486367 | KLD loss: 50.59735033247206
Epoch 973 | Age r2 val: -0.012524515390396118 | Age loss val: 0.21644505485892296

Epoch 984 | Age r2: -0.020237276951471966 | Age loss: 0.20739532924360699 |Age reg: 0.011472909374990396 | MSE loss: 488.07101270887586 | R2: 0.9437272532118691 | KLD loss: 50.56555758582221
Epoch 984 | Age r2 val: -0.01625305414199829 | Age loss val: 0.2159804217517376 | MSE loss val: 567.7711486816406 | R2 val: 0.932971403002739 | KLD loss val: 50.82691764831543
age_pred.shape, age.shape, batch.shape, x_rec.shape, x.shape torch.Size([64]) torch.Size([64]) torch.Size([64, 15812]) torch.Size([64, 15811]) torch.Size([64, 15811])
age_pred[0], age[0], batch_size, age_loss tensor(0.3396, device='cuda:0', grad_fn=<SelectBackward0>) tensor(0.5322, device='cuda:0') 64 tensor(0.2072, device='cuda:0', grad_fn=<SqrtBackward0>)
Epoch 985 | Age r2: -0.01198891798655192 | Age loss: 0.20749016975363097 |Age reg: 0.011479159377308356 | MSE loss: 490.71849483913843 | R2: 0.9432324369748434 | KLD loss: 50.46675290001763
Epoch 985 | Age r2 val: -0.014588028192520142 | Age loss val: 0.21693189442157745 |

Epoch 996 | Age r2: -0.03172465165456136 | Age loss: 0.20694896992709902 |Age reg: 0.011489884488077627 | MSE loss: 515.0826093885634 | R2: 0.9400558521350225 | KLD loss: 50.61063183678521
Epoch 996 | Age r2 val: -0.056780457496643066 | Age loss val: 0.21633830666542053 | MSE loss val: 609.1443023681641 | R2 val: 0.9271585941314697 | KLD loss val: 51.11543560028076
age_pred.shape, age.shape, batch.shape, x_rec.shape, x.shape torch.Size([64]) torch.Size([64]) torch.Size([64, 15812]) torch.Size([64, 15811]) torch.Size([64, 15811])
age_pred[0], age[0], batch_size, age_loss tensor(0.3399, device='cuda:0', grad_fn=<SelectBackward0>) tensor(0.5901, device='cuda:0') 64 tensor(0.1915, device='cuda:0', grad_fn=<SqrtBackward0>)
Epoch 997 | Age r2: -0.016763561301761203 | Age loss: 0.206820168842872 |Age reg: 0.011477473347137371 | MSE loss: 508.6880459255642 | R2: 0.9409194472763274 | KLD loss: 50.89851866828071
Epoch 997 | Age r2 val: -0.013745814561843872 | Age loss val: 0.2151610404253006 | M

In [9]:
metrics_history_max[-1], metrics_history_val_max[-1], seed_max

((0.29356812602943844, 0.9413665996657478),
 (0.33265067636966705, 0.9408136904239655),
 130)

In [11]:
SEED = seed_max
random.seed(SEED)
torch.manual_seed(SEED)
torch.cuda.manual_seed(SEED)
np.random.seed(SEED)
train_loader, val_loader, test_loader = split_trainValTest(datawNAN, batch_size, validation_split, test_split)
AgeModel = TwoLayerNetwork(latent_size, l1_lambda, l2_lambda, hidden_size)
vae = VAEAge(input_size, AgeModel, latent_size, down_channels, up_channels)
vae_optim = Adam(vae.parameters(), lr)
metrics_history, metrics_history_val = train_AgeVae(vae, train_loader, val_loader, batch_size, epochs, vae_optim, device)

age_pred.shape, age.shape, batch.shape, x_rec.shape, x.shape torch.Size([64]) torch.Size([64]) torch.Size([64, 15812]) torch.Size([64, 15811]) torch.Size([64, 15811])
age_pred[0], age[0], batch_size, age_loss tensor(1.9205, device='cuda:0', grad_fn=<SelectBackward0>) tensor(0.5734, device='cuda:0') 64 tensor(1.0680, device='cuda:0', grad_fn=<SqrtBackward0>)
Epoch 1 | Age r2: -26.374909771813286 | Age loss: 1.0704967280228932 |Age reg: 3.002906176779005 | MSE loss: 12712.418348524305 | R2: -0.47415562139617073 | KLD loss: 17.505935182174046
Epoch 1 | Age r2 val: -27.76443386077881 | Age loss val: 1.0837717652320862 | MSE loss val: 9234.87890625 | R2 val: -0.0592479407787323 | KLD loss val: 27.042251586914062
age_pred.shape, age.shape, batch.shape, x_rec.shape, x.shape torch.Size([64]) torch.Size([64]) torch.Size([64, 15812]) torch.Size([64, 15811]) torch.Size([64, 15811])
age_pred[0], age[0], batch_size, age_loss tensor(-0.5174, device='cuda:0', grad_fn=<SelectBackward0>) tensor(0.2078,

Epoch 12 | Age r2: -22.11264509624905 | Age loss: 0.9860804710123274 |Age reg: 2.5784953236579895 | MSE loss: 2677.1282619900176 | R2: 0.6890098849932352 | KLD loss: 54.454398261176216
Epoch 12 | Age r2 val: -22.364250659942627 | Age loss val: 0.9839758723974228 | MSE loss val: 2513.0502319335938 | R2 val: 0.7067611664533615 | KLD loss val: 55.9409704208374
age_pred.shape, age.shape, batch.shape, x_rec.shape, x.shape torch.Size([64]) torch.Size([64]) torch.Size([64, 15812]) torch.Size([64, 15811]) torch.Size([64, 15811])
age_pred[0], age[0], batch_size, age_loss tensor(-0.0450, device='cuda:0', grad_fn=<SelectBackward0>) tensor(0.5625, device='cuda:0') 64 tensor(0.9576, device='cuda:0', grad_fn=<SqrtBackward0>)
Epoch 13 | Age r2: -21.88808626598782 | Age loss: 0.9835392435391744 |Age reg: 2.541810545656416 | MSE loss: 2548.1197374131943 | R2: 0.7044342160224915 | KLD loss: 53.89374075995551
Epoch 13 | Age r2 val: -21.80416250228882 | Age loss val: 0.9771208465099335 | MSE loss val: 232

Epoch 24 | Age r2: -18.701695972018772 | Age loss: 0.9125876145230399 |Age reg: 2.1711353858311973 | MSE loss: 1836.52195570204 | R2: 0.7876423978143268 | KLD loss: 54.1177921295166
Epoch 24 | Age r2 val: -19.52042055130005 | Age loss val: 0.9205882847309113 | MSE loss val: 1786.0245361328125 | R2 val: 0.7926974296569824 | KLD loss val: 54.833786964416504
age_pred.shape, age.shape, batch.shape, x_rec.shape, x.shape torch.Size([64]) torch.Size([64]) torch.Size([64, 15812]) torch.Size([64, 15811]) torch.Size([64, 15811])
age_pred[0], age[0], batch_size, age_loss tensor(0.5599, device='cuda:0', grad_fn=<SelectBackward0>) tensor(0.2161, device='cuda:0') 64 tensor(0.9042, device='cuda:0', grad_fn=<SqrtBackward0>)
Epoch 25 | Age r2: -18.441704511642456 | Age loss: 0.900787838631206 |Age reg: 2.140766355726454 | MSE loss: 1816.5186157226562 | R2: 0.7890460938215256 | KLD loss: 54.682478480868866
Epoch 25 | Age r2 val: -19.90702724456787 | Age loss val: 0.9256545752286911 | MSE loss val: 1752.

Epoch 36 | Age r2: -16.30248996946547 | Age loss: 0.8529329945643743 |Age reg: 1.8367283311155107 | MSE loss: 1531.4212476942275 | R2: 0.822224121954706 | KLD loss: 55.003844790988495
Epoch 36 | Age r2 val: -17.18622636795044 | Age loss val: 0.8587452918291092 | MSE loss val: 1511.0547790527344 | R2 val: 0.8243803977966309 | KLD loss val: 55.39842414855957
age_pred.shape, age.shape, batch.shape, x_rec.shape, x.shape torch.Size([64]) torch.Size([64]) torch.Size([64, 15812]) torch.Size([64, 15811]) torch.Size([64, 15811])
age_pred[0], age[0], batch_size, age_loss tensor(-0.5843, device='cuda:0', grad_fn=<SelectBackward0>) tensor(0.1075, device='cuda:0') 64 tensor(0.9014, device='cuda:0', grad_fn=<SqrtBackward0>)
Epoch 37 | Age r2: -16.153735478719074 | Age loss: 0.8473939746618271 |Age reg: 1.8112996750407748 | MSE loss: 1511.502922905816 | R2: 0.824338835146692 | KLD loss: 55.16497410668267
Epoch 37 | Age r2 val: -17.21352529525757 | Age loss val: 0.8585565388202667 | MSE loss val: 1454

Epoch 48 | Age r2: -14.281042125489977 | Age loss: 0.7998413443565369 |Age reg: 1.5578203433089786 | MSE loss: 1320.091040717231 | R2: 0.8467535509003533 | KLD loss: 55.17810895707872
Epoch 48 | Age r2 val: -14.945405721664429 | Age loss val: 0.8037771135568619 | MSE loss val: 1307.2361450195312 | R2 val: 0.8487156480550766 | KLD loss val: 55.40986919403076
age_pred.shape, age.shape, batch.shape, x_rec.shape, x.shape torch.Size([64]) torch.Size([64]) torch.Size([64, 15812]) torch.Size([64, 15811]) torch.Size([64, 15811])
age_pred[0], age[0], batch_size, age_loss tensor(1.9712, device='cuda:0', grad_fn=<SelectBackward0>) tensor(0.7313, device='cuda:0') 64 tensor(0.8184, device='cuda:0', grad_fn=<SqrtBackward0>)
Epoch 49 | Age r2: -14.095001061757406 | Age loss: 0.7917142626312044 |Age reg: 1.536789122554991 | MSE loss: 1290.455084906684 | R2: 0.8501823362376955 | KLD loss: 55.30401399400499
Epoch 49 | Age r2 val: -14.749445915222168 | Age loss val: 0.7985701411962509 | MSE loss val: 126

...

Epoch 948 | Age r2: 0.3153423269589742 | Age loss: 0.1708064865734842 |Age reg: 0.0318407921327485 | MSE loss: 500.94986046685113 | R2: 0.941921580168936 | KLD loss: 50.75067276424832
Epoch 948 | Age r2 val: 0.3120282292366028 | Age loss val: 0.1661914773285389 | MSE loss val: 501.8954772949219 | R2 val: 0.9415432810783386 | KLD loss val: 50.635743141174316
age_pred.shape, age.shape, batch.shape, x_rec.shape, x.shape torch.Size([64]) torch.Size([64]) torch.Size([64, 15812]) torch.Size([64, 15811]) torch.Size([64, 15811])
age_pred[0], age[0], batch_size, age_loss tensor(0.3337, device='cuda:0', grad_fn=<SelectBackward0>) tensor(0.1974, device='cuda:0') 64 tensor(0.1580, device='cuda:0', grad_fn=<SqrtBackward0>)
Epoch 949 | Age r2: 0.31424493922127616 | Age loss: 0.1701399659117063 |Age reg: 0.03185649661140309 | MSE loss: 508.3910412258572 | R2: 0.9406996948851479 | KLD loss: 50.79761770036485
Epoch 949 | Age r2 val: 0.2925950586795807 | Age loss val: 0.16832121089100838 | MSE loss val:

Epoch 960 | Age r2: 0.3128300855557124 | Age loss: 0.17015182226896286 |Age reg: 0.0319625846006804 | MSE loss: 505.0171296861437 | R2: 0.9411783135599561 | KLD loss: 50.6032846238878
Epoch 960 | Age r2 val: 0.3004239499568939 | Age loss val: 0.16980767995119095 | MSE loss val: 516.8807830810547 | R2 val: 0.9391656517982483 | KLD loss val: 50.57448387145996
age_pred.shape, age.shape, batch.shape, x_rec.shape, x.shape torch.Size([64]) torch.Size([64]) torch.Size([64, 15812]) torch.Size([64, 15811]) torch.Size([64, 15811])
age_pred[0], age[0], batch_size, age_loss tensor(0.1597, device='cuda:0', grad_fn=<SelectBackward0>) tensor(0.5322, device='cuda:0') 64 tensor(0.1800, device='cuda:0', grad_fn=<SqrtBackward0>)
Epoch 961 | Age r2: 0.314737973941697 | Age loss: 0.17003412751687896 |Age reg: 0.031992912809881896 | MSE loss: 505.5845667521159 | R2: 0.9411438521411684 | KLD loss: 50.70511786142985
Epoch 961 | Age r2 val: 0.3023037016391754 | Age loss val: 0.16760987788438797 | MSE loss val:

Epoch 972 | Age r2: 0.3136993530723784 | Age loss: 0.17046868345803684 |Age reg: 0.03200298392524322 | MSE loss: 482.9830254448785 | R2: 0.944214842385716 | KLD loss: 50.62481011284722
Epoch 972 | Age r2 val: 0.3046637177467346 | Age loss val: 0.16806454211473465 | MSE loss val: 504.64737701416016 | R2 val: 0.9408280253410339 | KLD loss val: 50.45516872406006
age_pred.shape, age.shape, batch.shape, x_rec.shape, x.shape torch.Size([64]) torch.Size([64]) torch.Size([64, 15812]) torch.Size([64, 15811]) torch.Size([64, 15811])
age_pred[0], age[0], batch_size, age_loss tensor(0.2606, device='cuda:0', grad_fn=<SelectBackward0>) tensor(0.4375, device='cuda:0') 64 tensor(0.1671, device='cuda:0', grad_fn=<SqrtBackward0>)
Epoch 973 | Age r2: 0.31896715859572095 | Age loss: 0.1702040115164386 |Age reg: 0.03195962175312969 | MSE loss: 500.7214753892687 | R2: 0.9419973029030694 | KLD loss: 50.71834574805366
Epoch 973 | Age r2 val: 0.31548863649368286 | Age loss val: 0.16672095656394958 | MSE loss v

Epoch 984 | Age r2: 0.3257908870776494 | Age loss: 0.16867588584621748 |Age reg: 0.03196759273608526 | MSE loss: 485.2317360772027 | R2: 0.9435892618364758 | KLD loss: 50.8167527516683
Epoch 984 | Age r2 val: 0.287905752658844 | Age loss val: 0.16836309805512428 | MSE loss val: 533.3550033569336 | R2 val: 0.9380280077457428 | KLD loss val: 50.75206661224365
age_pred.shape, age.shape, batch.shape, x_rec.shape, x.shape torch.Size([64]) torch.Size([64]) torch.Size([64, 15812]) torch.Size([64, 15811]) torch.Size([64, 15811])
age_pred[0], age[0], batch_size, age_loss tensor(0.3383, device='cuda:0', grad_fn=<SelectBackward0>) tensor(0.3792, device='cuda:0') 64 tensor(0.1674, device='cuda:0', grad_fn=<SqrtBackward0>)
Epoch 985 | Age r2: 0.2790735082493888 | Age loss: 0.17430098230640093 |Age reg: 0.03188085121413072 | MSE loss: 525.9875038994683 | R2: 0.9388515369759666 | KLD loss: 50.58444828457303
Epoch 985 | Age r2 val: 0.29879094660282135 | Age loss val: 0.169570654630661 | MSE loss val: 

Epoch 996 | Age r2: 0.3242639634344313 | Age loss: 0.16933502794967759 |Age reg: 0.03185455666648017 | MSE loss: 495.44500139024524 | R2: 0.9424347480138143 | KLD loss: 50.70001061757406
Epoch 996 | Age r2 val: 0.26842983067035675 | Age loss val: 0.1687437929213047 | MSE loss val: 506.7210922241211 | R2 val: 0.9405915588140488 | KLD loss val: 50.71820259094238
age_pred.shape, age.shape, batch.shape, x_rec.shape, x.shape torch.Size([64]) torch.Size([64]) torch.Size([64, 15812]) torch.Size([64, 15811]) torch.Size([64, 15811])
age_pred[0], age[0], batch_size, age_loss tensor(0.3286, device='cuda:0', grad_fn=<SelectBackward0>) tensor(0.6042, device='cuda:0') 64 tensor(0.1867, device='cuda:0', grad_fn=<SqrtBackward0>)
Epoch 997 | Age r2: 0.3120501505004035 | Age loss: 0.17052628472447395 |Age reg: 0.031873186429341636 | MSE loss: 490.6252382066515 | R2: 0.9430725276470184 | KLD loss: 50.72440316942003
Epoch 997 | Age r2 val: 0.33932140469551086 | Age loss val: 0.16482727974653244 | MSE loss

In [ ]:
metrics_history_max[-1], metrics_history_val_max[-1], seed_max

In [ ]:
plt.plot( list(range(epochs)), metrics_history, color='r', label='Train')
plt.plot(list(range(epochs)), metrics_history_val, color='g', label='Validation')

plt.xlabel("Epochs")
plt.ylabel("R2")
plt.title("Training history")

plt.legend()
plt.show()

In [16]:
print([(len(data[data["Species"] == tis]), tis) for tis in data["Species"].unique()])

[(976, 'Mouse'), (453, 'Rat'), (1180, 'Human')]


In [29]:
data_test_mouse = data.fillna(0)[data['Species'] == "Mouse"]
data_test_mouse = torch.Tensor(data_test_mouse.select_dtypes(include=['float64']).iloc[:, :-1].values).to(device)
test_AgeVae(vae, data_test_mouse, device, age_weight = 1)

Loss 4812.46923828125 | Age r2: -0.6462159156799316 | Age loss: 0.21449925005435944 |Age reg: 0.031833793967962265 | MSE loss: 4806.91748046875 | R2: 0.22363334894180298 | KLD loss: 53.05558395385742


In [28]:
data_test_brain = data.fillna(0)[data['Species'] == "Human"]
data_test_brain = torch.Tensor(data_test_brain.select_dtypes(include=['float64']).iloc[:, :-1].values).to(device)
test_AgeVae(vae, data_test_brain, device, age_weight = 1)

Loss 5059.33837890625 | Age r2: 0.0606158971786499 | Age loss: 0.2098633050918579 |Age reg: 0.031833793967962265 | MSE loss: 5054.43798828125 | R2: 0.11995804309844971 | KLD loss: 46.588157653808594


In [27]:
data_test_rat = data.fillna(0)[data['Species'] == "Rat"]
data_test_rat = torch.Tensor(data_test_rat.select_dtypes(include=['float64']).iloc[:, :-1].values).to(device)
test_AgeVae(vae, data_test_rat, device, age_weight = 1)

Loss 6697.2431640625 | Age r2: 0.022563695907592773 | Age loss: 0.20779331028461456 |Age reg: 0.031833793967962265 | MSE loss: 6691.8154296875 | R2: -0.2952852249145508 | KLD loss: 51.87748336791992


In [26]:
data_test = data.fillna(0)
data_test = torch.Tensor(data_test.select_dtypes(include=['float64']).iloc[:, :-1].values).to(device)
test_AgeVae(vae, data_test, device, age_weight = 1)

Loss 399.41558837890625 | Age r2: 0.36187177896499634 | Age loss: 0.1663879156112671 |Age reg: 0.031833793967962265 | MSE loss: 394.1426086425781 | R2: 0.9551293849945068 | KLD loss: 50.74753952026367


In [ ]:
X_embedded = TSNE(n_components=2, init='random').fit_transform(datawNAN[:, :-1].cpu().numpy())

In [ ]:
d = {'t-SNE1': X_embedded[:, 0], 't-SNE2': X_embedded[:, 1], 'Age': data["Age_rel_m"]}
df = pd.DataFrame(data=d)

In [ ]:
sns.scatterplot(data=df, x="t-SNE1", y="t-SNE2", hue="Age")
sns.set(rc={'figure.figsize':(10.7,20.27)})

In [ ]:
x = vae.encode(datawNAN[:, :-1].cuda())
x.shape

In [ ]:
corr = np.concatenate([x.cpu().detach().numpy(), datawNAN[:, -1].reshape((-1, 1)).cpu().detach().numpy()], axis = 1)
corr.shape

In [ ]:
corrcoef = np.corrcoef(corr, rowvar = False)
corrcoef.shape

In [ ]:
ax = sns.heatmap(corrcoef, annot=True)

In [ ]:
vae_embedded = TSNE(n_components=2, init='random').fit_transform(x.cpu().detach().numpy())

In [ ]:
d_vae = {'t-SNE1': vae_embedded[:, 0], 't-SNE2': vae_embedded[:, 1], 'Age': data["Age_rel_m"]}
df_vae = pd.DataFrame(data=d_vae)

In [ ]:
sns.scatterplot(data=df_vae, x="t-SNE1", y="t-SNE2", hue="Age")
sns.set(rc={'figure.figsize':(10.7,10.27)})